In [ ]:
import MetaTrader5 as mt5
from dotenv import load_dotenv
import os

# Load environment variables from the .env file
load_dotenv()

# Retrieve credentials securely
MT5_PATH = os.getenv("MT5_PATH", r"C:\Program Files\MetaTrader 5\terminal64.exe")
MT5_ACCOUNT = os.getenv("MT5_ACCOUNT")
MT5_PASSWORD = os.getenv("MT5_PASSWORD")
MT5_SERVER = os.getenv("MT5_SERVER")

# Initialize MetaTrader 5
mt5.initialize(path=MT5_PATH)
print("MetaTrader5 package author:", mt5.__author__)
print("MetaTrader5 package version:", mt5.__version__)

# Try logging in using environment credentials
authorized = mt5.login(account=int(MT5_ACCOUNT), password=MT5_PASSWORD, server=MT5_SERVER)

if authorized:
    print(mt5.account_info())
    print("\nShow account_info()._asdict():")
    account_info_dict = mt5.account_info()._asdict()
    for prop, value in account_info_dict.items():
        print(f"  {prop}={value}")
else:
    print(f"Failed to connect at account #{MT5_ACCOUNT}, error code: {mt5.last_error()}")


MetaTrader5 package author: MetaQuotes Ltd.
MetaTrader5 package version: 5.0.45


In [ ]:
import MetaTrader5 as mt5
import pandas as pd
from datetime import datetime, timedelta
import os


In [7]:
# -------------------------------------------------------------------------
# Inicializar o MetaTrader 5
# -------------------------------------------------------------------------
if not mt5.initialize():
    print("Falha ao inicializar o MetaTrader 5:", mt5.last_error())
    quit()

# -------------------------------------------------------------------------
# Configurações
# -------------------------------------------------------------------------
symbol = "XAUUSD"

# Data de início e fim (dias locais, UTC−2)
local_start_date = datetime(2020, 1, 1)
local_end_date = datetime(2025, 6, 8)

# Pasta para salvar os arquivos
folder_path = f"raw/candles/{symbol}"
os.makedirs(folder_path, exist_ok=True)

# -------------------------------------------------------------------------
# Loop para capturar dados por intervalos de dias
# -------------------------------------------------------------------------
date_range = pd.date_range(local_start_date, local_end_date, freq="D")
for single_date in date_range:
    # Definir os intervalos de tempo para o dia local (UTC−2)
    local_day_start = single_date.replace(hour=0, minute=0, second=0, microsecond=0)
    local_day_end = single_date.replace(hour=23, minute=59, second=59, microsecond=999999)
    
    # Converter para UTC somando 2 horas
    utc_day_start = local_day_start + timedelta(hours=6)
    utc_day_end = local_day_end + timedelta(hours=6)

    print(f"\nCapturando rates de {symbol} no dia local {local_day_start.strftime('%Y-%m-%d')} (UTC {utc_day_start.strftime('%Y-%m-%d %H:%M:%S')} - {utc_day_end.strftime('%Y-%m-%d %H:%M:%S')})")

    rates = mt5.copy_rates_range("XAUUSD", mt5.TIMEFRAME_M30, utc_day_start, utc_day_end)
    print(rates)
    if rates is None or rates.size == 0:
        print("Nenhum rates encontrado nesse dia.")
        continue

    df = pd.DataFrame(rates)

    df['time'] = pd.to_datetime(df['time'], unit='s', utc=True)

    # Ajustar o tempo para o fuso horário local (UTC−2)
    df['time'] = df['time'] - timedelta(hours=6)

    df = df.sort_values(by='time').reset_index(drop=True)

    # Nome do arquivo baseado na data local
    date_str = local_day_start.strftime('%Y-%m-%d')


    csv_filepath = os.path.join(folder_path, f"{symbol}_{date_str}.csv")
    df.to_csv(csv_filepath, index=False)
    print(f"  Dados salvos em: {csv_filepath}")

mt5.shutdown()



Capturando rates de XAUUSD no dia local 2020-01-01 (UTC 2020-01-01 06:00:00 - 2020-01-02 05:59:59)
[]
Nenhum rates encontrado nesse dia.

Capturando rates de XAUUSD no dia local 2020-01-02 (UTC 2020-01-02 06:00:00 - 2020-01-03 05:59:59)
[(1577944800, 1520.26, 1520.36, 1519.77, 1519.81,  308, 21, 0)
 (1577946600, 1519.81, 1520.05, 1519.39, 1519.39,  448, 20, 0)
 (1577948400, 1519.37, 1519.71, 1518.95, 1519.47,  531, 19, 0)
 (1577950200, 1519.53, 1520.36, 1518.95, 1520.19,  917, 21, 0)
 (1577952000, 1520.2 , 1520.81, 1519.81, 1520.09,  795, 20, 0)
 (1577953800, 1520.15, 1520.91, 1519.3 , 1520.87, 1174, 21, 0)
 (1577955600, 1520.94, 1521.37, 1519.18, 1519.57, 1973, 19, 0)
 (1577957400, 1519.49, 1520.31, 1519.03, 1519.11, 1484, 20, 0)
 (1577959200, 1519.11, 1520.46, 1518.38, 1519.38, 2088, 17, 0)
 (1577961000, 1519.38, 1520.93, 1519.3 , 1520.75, 2121, 20, 0)
 (1577962800, 1520.75, 1520.93, 1519.52, 1520.34, 1642, 22, 0)
 (1577964600, 1520.34, 1521.35, 1520.32, 1520.6 , 1401, 22, 0)
 (1577

True